In [1]:
import pandas as pd
from sklearn.model_selection import train_test_split
import tensorflow as tf

In [2]:
df = pd.read_csv('SMSSpamCollection' , sep='\t' , names=['label' , 'message'])
df.head()

label                                            message
0   ham  Go until jurong point, crazy.. Available only ...
1   ham                      Ok lar... Joking wif u oni...
2  spam  Free entry in 2 a wkly comp to win FA Cup fina...
3   ham  U dun say so early hor... U c already then say...
4   ham  Nah I don't think he goes to usf, he lives aro...

In [3]:
df.shape

(5572, 2)

In [4]:
x = list(df['message'])
y = list(df['label'])

In [5]:
x[:5]

['Go until jurong point, crazy.. Available only in bugis n great world la e buffet... Cine there got amore wat...',
 'Ok lar... Joking wif u oni...',
 "Free entry in 2 a wkly comp to win FA Cup final tkts 21st May 2005. Text FA to 87121 to receive entry question(std txt rate)T&C's apply 08452810075over18's",
 'U dun say so early hor... U c already then say...',
 "Nah I don't think he goes to usf, he lives around here though"]

In [6]:
y[:5]

['ham', 'ham', 'spam', 'ham', 'ham']

In [7]:
y = list(pd.get_dummies(y)['spam'])
y[:5]

[0, 0, 1, 0, 0]

In [8]:
x_train , x_test , y_train , y_test = train_test_split(x , y  ,test_size = 0.2 , random_state=0)

In [9]:
len(x_train)

4457

In [10]:
len(x_test)

1115

In [11]:
from transformers import DistilBertTokenizerFast
tokenizer = DistilBertTokenizerFast.from_pretrained('distilbert-base-uncased')

tokenizer_config.json:   0%|          | 0.00/28.0 [00:00<?, ?B/s]

vocab.txt:   0%|          | 0.00/232k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/466k [00:00<?, ?B/s]

config.json:   0%|          | 0.00/483 [00:00<?, ?B/s]

In [12]:
train_encoding = tokenizer(x_train , truncation=True , padding=True)
test_encoding = tokenizer(x_test , truncation=True , padding=True)

In [13]:
train_dataset = tf.data.Dataset.from_tensor_slices((
      dict(train_encoding),
                  y_train
      ))

test_dataset = tf.data.Dataset.from_tensor_slices((
    dict(test_encoding),
                    y_test
    ))

In [14]:
id2label = {0: "ham", 1: "spam"}
label2id = {"ham": 0, "spam": 1}

In [15]:
test_dataset

<_TensorSliceDataset element_spec=({'input_ids': TensorSpec(shape=(221,), dtype=tf.int32, name=None), 'attention_mask': TensorSpec(shape=(221,), dtype=tf.int32, name=None)}, TensorSpec(shape=(), dtype=tf.int32, name=None))>

In [16]:

from transformers import TFDistilBertForSequenceClassification , TFTrainer , TFTrainingArguments

training_args = TFTrainingArguments(
    output_dir = './results',
    num_train_epochs = 2,
    per_device_train_batch_size = 8,
    per_device_eval_batch_size = 16,
    eval_steps=100,
    warmup_steps = 500,
    weight_decay = 0.01,
    logging_dir = './logs',
    logging_steps = 10,
)

In [17]:

with training_args.strategy.scope():
  model = TFDistilBertForSequenceClassification.from_pretrained('distilbert-base-uncased',id2label=id2label, label2id=label2id)

trainer = TFTrainer(
    model = model,
    args = training_args,
    train_dataset = train_dataset,
    eval_dataset = test_dataset
)

model.config.use_cache = False
trainer.train()


model.safetensors:   0%|          | 0.00/268M [00:00<?, ?B/s]

Some weights of the PyTorch model were not used when initializing the TF 2.0 model TFDistilBertForSequenceClassification: ['vocab_transform.bias', 'vocab_transform.weight', 'vocab_layer_norm.bias', 'vocab_projector.bias', 'vocab_layer_norm.weight']
- This IS expected if you are initializing TFDistilBertForSequenceClassification from a PyTorch model trained on another task or with another architecture (e.g. initializing a TFBertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing TFDistilBertForSequenceClassification from a PyTorch model that you expect to be exactly identical (e.g. initializing a TFBertForSequenceClassification model from a BertForSequenceClassification model).
Some weights or buffers of the TF 2.0 model TFDistilBertForSequenceClassification were not initialized from the PyTorch model and are newly initialized: ['pre_classifier.weight', 'pre_classifier.bias', 'classifier.weight', 'classifier.bias']
You should 

In [18]:
trainer.evaluate(test_dataset)

{'eval_loss': 0.017569826330457415}

In [19]:
trainer.predict(test_dataset)

PredictionOutput(predictions=array([[ 3.8966346, -3.0628417],
       [-2.890867 ,  2.7945273],
       [ 3.6326494, -2.8260531],
       ...,
       [ 3.1717052, -2.436365 ],
       [-2.9046443,  2.8221161],
       [ 3.3059733, -2.4722457]], dtype=float32), label_ids=array([0, 1, 0, ..., 0, 1, 0], dtype=int32), metrics={'eval_loss': 0.017577954701014926})

In [20]:
y_out = trainer.predict(test_dataset)[1]

In [21]:
from sklearn.metrics import confusion_matrix

confusion_matrix(y_test , y_out)

array([[955,   0],
       [  0, 160]])

In [22]:
from sklearn.metrics import classification_report

print(classification_report(y_test , y_out))

              precision    recall  f1-score   support

           0       1.00      1.00      1.00       955
           1       1.00      1.00      1.00       160

    accuracy                           1.00      1115
   macro avg       1.00      1.00      1.00      1115
weighted avg       1.00      1.00      1.00      1115



In [23]:
from huggingface_hub import notebook_login

notebook_login()

In [24]:
model.push_to_hub('sentiment_fine_tune_bert')

tf_model.h5:   0%|          | 0.00/268M [00:00<?, ?B/s]

In [25]:
tokenizer.push_to_hub('sentiment_fine_tune_bert')

CommitInfo(commit_url='https://huggingface.co/sweetpablo/sentiment_fine_tune_bert/commit/f24d23c183e7d51dc08c5014ffaf737ebcaa6f4d', commit_message='Upload tokenizer', commit_description='', oid='f24d23c183e7d51dc08c5014ffaf737ebcaa6f4d', pr_url=None, pr_revision=None, pr_num=None)